In [56]:
import TOSICA
import scanpy as sc
import numpy as np
import warnings 
warnings.filterwarnings ("ignore")
import pandas as pd
import os


In [2]:
import torch
print(torch.__version__)


2.0.1


False

### Read in datasets

In [62]:
input_healthy = '/Users/anna.maguza/Desktop/Data/Processed_datasets/Cancer_dataset_integration/input_files/Epithelial_cells/Epithelial_Healthy_anndata_normalized_3K.h5ad'
Healthy_adata = sc.read(input_healthy)

In [63]:
input_cancer = '/Users/anna.maguza/Desktop/Data/Processed_datasets/Cancer_dataset_integration/input_files/Epithelial_cells/Epithelial_Colon_cancer_atlas_normalized_3K.h5ad'
Cancer_adata = sc.read(input_cancer)

In [64]:
# Read gmt file
with open('/Users/anna.maguza/TOSICA/TOSICA/resources/GO_bp.gmt') as gmt:
    print(gmt.read())

GOBP_MITOCHONDRIAL_GENOME_MAINTENANCE	http://www.gsea-msigdb.org/gsea/msigdb/cards/GOBP_MITOCHONDRIAL_GENOME_MAINTENANCE	AKT3	PPARGC1A	POLG2	PARP1	DNA2	TYMP	PRIMPOL	STOX1	SLC25A4	LIG3	MEF2A	MPV17	OPA1	SLC25A36	TOP3A	TP53	PIF1	SESN2	SLC25A33	MGME1	LONP1
GOBP_REPRODUCTION	http://www.gsea-msigdb.org/gsea/msigdb/cards/GOBP_REPRODUCTION	ADA	GNPDA1	ZGLP1	SYCE1L	BSPH1	PLA2G4B	BCL2L10	BCL2L11	TSPY10	MAMLD1	APELA	RNF212B	SMC4	ACTR3	ACTR2	TCP11X1	RAD50	FEM1B	ACTR1A	BCAP31	ADGRG2	TRIM28	CDK2	RBM7	LHFPL2	CCDC182	MEI4	ADAM10	IRX5	RAMP2	FSTL3	PKDREJ	NPM2	CITED2	SEMA3A	SYCP2	WFDC2	SPAG11B	BASP1	TESK2	TUBGCP3	CDX2	CDX4	MERTK	FST	CLGN	HOXB13	CRTAP	UNC13B	CEBPA	CEBPB	CIB1	DEAF1	PRDX4	AKAP3	CCT7	CCT4	CCT2	SMC2	CENPC	P3H4	RAD51AP1	SPINT2	DMRT2	KHDRBS1	CELF1	KLF1	CETN2	CCT8	CORIN	TCFL5	PLK4	STAG3	STAG2	PTTG2	PLAC1	KDM5B	TOB2	CFTR	FRS2	CGB3	TUBGCP2	ADAM28	EDDM3A	ADCY3	MAGED2	SPIN1	PRDX3	PRSS21	TMED2	CCNI	SLC38A3	IFT27	TDRKH	ZPBP	ABHD2	SOX30	HSF2BP	ADAM30	ADAM29	PRDM7	DMC1	PTGDR2	ADCY7	PLCD3	PARK7	PHB2	AZIN2

### Model Train

In [65]:
#Extract the 5% of the dataset to check the performance of the model
Healthy_adata = Healthy_adata[:150]
Cancer_adata = Cancer_adata[:150]

In [66]:
# Load your adata.var as a DataFrame
adata_var = pd.DataFrame(Healthy_adata.var) # replace with your actual path

# Extract gene names from adata.var
adata_genes = set(adata_var['gene_name-Kong'])  # replace 'gene_names' with your actual column name

# Load your GMT file
with open('/Users/anna.maguza/TOSICA/TOSICA/resources/GO_bp.gmt') as f:
    gmt_content = f.readlines()

# Extract gene names from GMT file
gmt_genes = set()
for line in gmt_content:
    genes_in_line = line.strip().split('\t')[2:]  # the first two entries are not genes
    gmt_genes.update(genes_in_line)

# Find genes in GMT file that are not in adata.var
extra_genes = gmt_genes - adata_genes

extra_genes2 = adata_genes - gmt_genes

print(f"There are {len(extra_genes)} genes in the GMT file that are not in adata.var.")
print(f"There are {len(extra_genes2)} genes in adata.var that are not in the GMT file.")

There are 15863 genes in the GMT file that are not in adata.var.
There are 751 genes in adata.var that are not in the GMT file.


In [67]:
# Create a new GMT file
with open('/Users/anna.maguza/TOSICA/TOSICA/resources/GO_bp_filtered.gmt', 'w') as f_out:
    for line in gmt_content:
        elements = line.strip().split('\t')
        gene_set_name = elements[0]
        description = elements[1]
        genes = elements[2:]
        
        # Only include genes that are in adata.var
        filtered_genes = [gene for gene in genes if gene in adata_genes]
        
        if filtered_genes:  # Only write gene sets that have at least one gene
            f_out.write('\t'.join([gene_set_name, description] + filtered_genes) + '\n')

# Get the list of genes in the GMT file
gmt_genes = set()
for line in gmt_content:
    elements = line.strip().split('\t')
    genes = elements[2:]
    gmt_genes.update(genes)

# Filter adata.var to only include genes that are in the GMT file
Healthy_adata = Healthy_adata[:, Healthy_adata.var.index.isin(gmt_genes)]

In [68]:
# Load your adata.var as a DataFrame
adata_var = pd.DataFrame(Healthy_adata.var) # replace with your actual path

# Extract gene names from adata.var
adata_genes = set(adata_var['gene_name-Kong'])  # replace 'gene_names' with your actual column name

# Load your GMT file
with open('/Users/anna.maguza/TOSICA/TOSICA/resources/GO_bp_filtered.gmt') as f:
    gmt_content = f.readlines()

# Extract gene names from GMT file
gmt_genes = set()
for line in gmt_content:
    genes_in_line = line.strip().split('\t')[2:]  # the first two entries are not genes
    gmt_genes.update(genes_in_line)

# Find genes in GMT file that are not in adata.var
extra_genes = gmt_genes - adata_genes

extra_genes2 = adata_genes - gmt_genes

print(f"There are {len(extra_genes)} genes in the GMT file that are not in adata.var.")
print(f"There are {len(extra_genes2)} genes in adata.var that are not in the GMT file.")

There are 0 genes in the GMT file that are not in adata.var.
There are 0 genes in adata.var that are not in the GMT file.


In [69]:
# Load your adata.var as a DataFrame
adata_var = pd.DataFrame(Cancer_adata.var) # replace with your actual path

# Extract gene names from adata.var
adata_genes = set(adata_var['gene_name'])  # replace 'gene_names' with your actual column name

# Load your GMT file
with open('/Users/anna.maguza/TOSICA/TOSICA/resources/GO_bp_filtered.gmt') as f:
    gmt_content = f.readlines()

# Extract gene names from GMT file
gmt_genes = set()
for line in gmt_content:
    genes_in_line = line.strip().split('\t')[2:]  # the first two entries are not genes
    gmt_genes.update(genes_in_line)

# Find genes in GMT file that are not in adata.var
extra_genes = gmt_genes - adata_genes

extra_genes2 = adata_genes - gmt_genes

print(f"There are {len(extra_genes)} genes in the GMT file that are not in adata.var.")
print(f"There are {len(extra_genes2)} genes in adata.var that are not in the GMT file.")

There are 0 genes in the GMT file that are not in adata.var.
There are 751 genes in adata.var that are not in the GMT file.


In [70]:
# Get the list of genes in the GMT file
gmt_genes = set()
for line in gmt_content:
    elements = line.strip().split('\t')
    genes = elements[2:]
    gmt_genes.update(genes)

# Filter adata.var to only include genes that are in the GMT file
Cancer_adata = Cancer_adata[:, Cancer_adata.var.index.isin(gmt_genes)]

In [61]:
TOSICA.train(Healthy_adata, gmt_path='/Users/anna.maguza/TOSICA/TOSICA/resources/GO_bp_filtered.gmt', label_name='Unified Cell States', epochs=3, project='hGOBP_demo' )
!ls ./hGOBP_demo

cpu


KeyError: 'Unified Cell States'

In [23]:
# Load the CSV file into a pandas DataFrame
df = pd.read_csv('/Users/anna.maguza/Desktop/GCA_social_network/5_cancer_data_integration/5.5_TOSICA_labels_transfer/hGOBP_demo/gene2token_weights.csv', header=None)

# Print the first few rows of the DataFrame
print(df.head())

# Make the row 0 the header
df.columns = df.iloc[0]
# Delete row 0
df = df.iloc[1:]

# Make the column 0 the index
df.index = df.iloc[:, 0]
# Delete column 0
df = df.iloc[:, 1:]

                                                0    1      2      3      
0                                                  0  SLN  PTGDS  GSTA1  \
1                                  GOBP_REPRODUCTION  0.0    0.0    0.0   
2  GOBP_NEGATIVE_REGULATION_OF_TRANSCRIPTION_BY_R...  0.0    0.0    0.0   
3                                  GOBP_MAPK_CASCADE  0.0    0.0    0.0   
4                            GOBP_MITOTIC_CELL_CYCLE  0.0    0.0    0.0   

      4       5     6            7     8            9     ...     2077   2078   
0  AKR1B10  CHST13  MUC4       HSPA1B  CTSG  KLRC4-KLRK1  ...  ONECUT3  ISG20  \
1      0.0     0.0   0.0          0.0   0.0          0.0  ...      0.0    0.0   
2      0.0     0.0   0.0          0.0   0.0          0.0  ...      0.0    0.0   
3      0.0     0.0   0.0          0.0   0.0          0.0  ...      0.0    0.0   
4      0.0     0.0   0.0  0.021805082   0.0          0.0  ...      0.0    0.0   

          2079   2080   2081   2082    2083         2084     2

In [28]:
# Load the model
model = torch.load('/Users/anna.maguza/Desktop/GCA_social_network/5_cancer_data_integration/5.5_TOSICA_labels_transfer/hGOBP_demo/model-0.pth')

# Print the model structure
print(model)

OrderedDict([('cls_token', tensor([[[ 1.9388e-02,  1.3120e-02,  1.6317e-02, -2.0314e-02, -1.9601e-03,
           9.9638e-03, -9.4630e-03, -3.3581e-02, -5.0975e-04,  1.6750e-03,
           2.8711e-02, -1.4301e-02,  1.8046e-02,  8.3085e-03, -1.9064e-02,
          -2.7346e-04, -2.4332e-03, -3.8927e-03, -2.7253e-02, -1.7643e-02,
           1.4988e-03,  2.4697e-02,  1.6047e-02,  7.7555e-03, -1.6061e-02,
          -5.7731e-02, -2.0929e-02,  2.2252e-02, -1.2050e-02,  2.4432e-02,
           7.0770e-03, -2.8555e-02, -3.7163e-04,  2.1989e-02,  1.7156e-02,
           2.8745e-02,  1.8626e-02, -6.3671e-05, -1.5955e-03, -7.6100e-03,
           2.9195e-02,  6.0727e-02, -1.3503e-02,  5.6793e-03,  2.0031e-02,
          -2.9035e-03, -3.6255e-02, -3.5433e-02]]])), ('feature_embed.fe.mask', tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        ...,
        [1., 1., 1.,  ..., 1., 1., 1.],
        [1., 1., 1.,  ..., 1., 1., 1.],
     

In [38]:
# Load the model weights
model_weights = np.load('/Users/anna.maguza/Desktop/GCA_social_network/5_cancer_data_integration/5.5_TOSICA_labels_transfer/hGOBP_demo/model-0.pth')

In [41]:
# Load the model weights
model_weights = np.load('/Users/anna.maguza/Desktop/GCA_social_network/5_cancer_data_integration/5.5_TOSICA_labels_transfer/hGOBP_demo/model-0.pth')

pathway = pd.read_csv('/Users/anna.maguza/Desktop/GCA_social_network/5_cancer_data_integration/5.5_TOSICA_labels_transfer/hGOBP_demo/pathway.csv', index_col=0)
att = torch.empty([0,(len(pathway))]).cpu()
print("Shape of att:", att.shape)

Shape of att: torch.Size([0, 300])


In [42]:
varinfo = pd.DataFrame(pathway.iloc[0:len(pathway),0].values,index=pathway.iloc[0:len(pathway),0],columns=['pathway_index'])
print("Shape of varinfo:", varinfo.shape)

Shape of varinfo: (300, 1)


In [50]:
def prediect2(adata,model_weight_path,project,mask_path,laten=False,save_att = 'X_att', save_lantent = 'X_lat',n_step=10000,cutoff=0.1,n_unannotated = 1,batch_size = 50,embed_dim=48,depth=2,num_heads=4):
    device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
    print(device)
    num_genes = adata.shape[1]
    #mask_path = os.getcwd()+project+'/mask.npy'
    mask = np.load(mask_path)
    project_path = os.getcwd()+'/%s'%project
    pathway = pd.read_csv(project_path+'/pathway.csv', index_col=0)
    dictionary = pd.read_table(project_path+'/label_dictionary.csv', sep=',',header=0,index_col=0)
    n_c = len(dictionary)
    label_name = dictionary.columns[0]
    dictionary.loc[(dictionary.shape[0])] = 'Unknown'
    dic = {}
    for i in range(len(dictionary)):
        dic[i] = dictionary[label_name][i]
    model = create_model(num_classes=n_c, num_genes=num_genes,mask = mask, has_logits=False,depth=depth,num_heads=num_heads).to(device)
    # load model weights
    model.load_state_dict(torch.load(model_weight_path, map_location=device))
    model.eval()
    parm={}
    for name,parameters in model.named_parameters():
        #print(name,':',parameters.size())
        parm[name]=parameters.detach().cpu().numpy()
    gene2token = parm['feature_embed.fe.weight']
    gene2token = gene2token.reshape((int(gene2token.shape[0]/embed_dim),embed_dim,adata.shape[1]))
    gene2token = abs(gene2token)
    gene2token = np.max(gene2token,axis=1)
    gene2token = pd.DataFrame(gene2token)
    gene2token.columns=adata.var_names
    gene2token.index = pathway['0']
    gene2token.to_csv(project_path+'/gene2token_weights.csv')
    latent = torch.empty([0,embed_dim]).cpu()
    att = torch.empty([0,(len(pathway))]).cpu()
    predict_class = np.empty(shape=0)
    pre_class = np.empty(shape=0)      
    latent = torch.squeeze(latent).cpu().numpy()
    l_p = np.c_[latent, predict_class,pre_class]
    att = np.c_[att, predict_class,pre_class]
    all_line = adata.shape[0]
    n_line = 0
    adata_list = []
    while (n_line) <= all_line:
        if (all_line-n_line)%batch_size != 1:
            expdata = pd.DataFrame(todense(adata[n_line:n_line+min(n_step,(all_line-n_line))]),index=np.array(adata[n_line:n_line+min(n_step,(all_line-n_line))].obs_names).tolist(), columns=np.array(adata.var_names).tolist())
            print(n_line)
            n_line = n_line+n_step
        else:
            expdata = pd.DataFrame(todense(adata[n_line:n_line+min(n_step,(all_line-n_line-2))]),index=np.array(adata[n_line:n_line+min(n_step,(all_line-n_line-2))].obs_names).tolist(), columns=np.array(adata.var_names).tolist())
            n_line = (all_line-n_line-2)
            print(n_line)
        expdata = np.array(expdata)
        expdata = torch.from_numpy(expdata.astype(np.float32))
        data_loader = torch.utils.data.DataLoader(expdata,
                                                 batch_size=batch_size,
                                                 shuffle=False,
                                                 pin_memory=True)
        with torch.no_grad():
            # predict class
            for step, data in enumerate(data_loader):
                #print(step)
                exp = data
                lat, pre, weights = model(exp.to(device))
                pre = torch.squeeze(pre).cpu()
                pre = F.softmax(pre,1)
                predict_class = np.empty(shape=0)
                pre_class = np.empty(shape=0) 
                for i in range(len(pre)):
                    if torch.max(pre, dim=1)[0][i] >= cutoff: 
                        predict_class = np.r_[predict_class,torch.max(pre, dim=1)[1][i].numpy()]
                    else:
                        predict_class = np.r_[predict_class,n_c]
                    pre_class = np.r_[pre_class,torch.max(pre, dim=1)[0][i]]     
                l_p = torch.squeeze(lat).cpu().numpy()
                att = torch.squeeze(weights).cpu().numpy()
                meta = np.c_[predict_class,pre_class]
                meta = pd.DataFrame(meta)
                meta.columns = ['Prediction','Probability']
                meta.index = meta.index.astype('str')
                if laten:
                    l_p = l_p.astype('float32')
                    new = sc.AnnData(l_p, obs=meta)
                else:
                    att = att[:,0:(len(pathway)-n_unannotated)]
                    att = att.astype('float32')
                    varinfo = pd.DataFrame(pathway.iloc[0:len(pathway),0].values,index=pathway.iloc[0:len(pathway),0],columns=['pathway_index'])
                    new = sc.AnnData(att, obs=meta, var = varinfo)
                adata_list.append(new)
    print(all_line)
    new = ad.concat(adata_list)
    new.obs.index = adata.obs.index
    new.obs['Prediction'] = new.obs['Prediction'].map(dic)
    new.obs[adata.obs.columns] = adata.obs[adata.obs.columns].values
    return(new)

In [51]:
model_weight_path = './hGOBP_demo/model-0.pth'
new_adata = prediect2(Cancer_adata, model_weight_path = model_weight_path, mask_path = '/Users/anna.maguza/Desktop/GCA_social_network/5_cancer_data_integration/5.5_TOSICA_labels_transfer/hGOBP_demo/mask.npy', project='hGOBP_demo')

cpu


AttributeError: module 'TOSICA' has no attribute 'create_model'